# Submission 1: Stress Detection from Social Media Articles

## Import Library

In [1]:
import tensorflow as tf
from tfx.components import CsvExampleGen, StatisticsGen, SchemaGen, ExampleValidator, Transform, Trainer, Tuner
from tfx.proto import example_gen_pb2
from tfx.orchestration.experimental.interactive.interactive_context import InteractiveContext
import os

## Set Variable
Code ini mengatur konfigurasi dan path untuk menyimpan artefak yang dihasilkan selama eksekusi pipeline untuk deteksi stres, termasuk direktori untuk menyimpan pipeline, basis data metadata untuk menyimpan metadata MLMD (Machine Learning Metadata), serta direktori output untuk menyimpan model-model yang dihasilkan dari pipeline tersebut.

In [2]:
PIPELINE_NAME = "jericho_luthfi_ihFK-pipeline"
SCHEMA_PIPELINE_NAME = "fake-news-schema"

#Directory untuk menyimpan artifact yang akan dihasilkan
PIPELINE_ROOT = os.path.join('pipelines', PIPELINE_NAME)

# Path to a SQLite DB file to use as an MLMD storage.
METADATA_PATH = os.path.join('metadata', PIPELINE_NAME, 'metadata.db')

# Output directory where created models from the pipeline will be exported.
SERVING_MODEL_DIR = os.path.join('serving_model', PIPELINE_NAME)

# from absl import logging
# logging.set_verbosity(logging.INFO)

In [3]:
DATA_ROOT = "data"

In [4]:
import pandas as pd
df = pd.read_csv(r'C:\Users\ANANG\ML_Ops\Jericho Submission 1\data\data.csv')
df

URLs  \
0     http://www.bbc.com/news/world-us-canada-414191...   
1     https://www.reuters.com/article/us-filmfestiva...   
2     https://www.nytimes.com/2017/10/09/us/politics...   
3     https://www.reuters.com/article/us-mexico-oil-...   
4     http://www.cnn.com/videos/cnnmoney/2017/10/08/...   
...                                                 ...   
4004  http://beforeitsnews.com/sports/2017/09/trends...   
4005  http://beforeitsnews.com/u-s-politics/2017/10/...   
4006  https://www.activistpost.com/2017/09/ron-paul-...   
4007  https://www.reuters.com/article/us-china-pharm...   
4008  http://beforeitsnews.com/u-s-politics/2017/10/...   

                                               Headline  \
0            Four ways Bob Corker skewered Donald Trump   
1     Linklater's war veteran comedy speaks to moder...   
2     Trump’s Fight With Corker Jeopardizes His Legi...   
3     Egypt's Cheiron wins tie-up with Pemex for Mex...   
4           Jason Aldean opens 'SNL' with Vegas tribute   
...                                                 ...   
4004                                    Trends to Watch   
4005  Trump Jr. Is Soon To Give A 30-Minute Speech F...   
4006        Ron Paul on Trump, Anarchism & the AltRight   
4007  China to accept overseas trial data in bid to ...   
4008  Vice President Mike Pence Leaves NFL Game Beca...   

                                                   Body  Label  
0     Image copyright Getty Images\nOn Sunday mornin...      1  
1     LONDON (Reuters) - “Last Flag Flying”, a comed...      1  
2     The feud broke into public view last week when...      1  
3     MEXICO CITY (Reuters) - Egypt’s Cheiron Holdin...      1  
4     Country singer Jason Aldean, who was performin...      1  
...                                                 ...    ...  
4004  Trends to Watch\n% of readers think this story...      0  
4005  Trump Jr. Is Soon To Give A 30-Minute Speech F...      0  
4006                                                NaN      0  
4007  SHANGHAI (Reuters) - China said it plans to ac...      1  
4008  Vice President Mike Pence Leaves NFL Game Beca...      0  

[4009 rows x 4 columns]

In [5]:
interactive_context = InteractiveContext(pipeline_root=PIPELINE_ROOT)

## Data Ingestion

### ExampleGen
Code ini mengatur konfigurasi output untuk `CsvExampleGen`, yang membagi data dari `DATA_ROOT` menjadi dua bagian: `train` dengan 8 hash buckets dan `eval` dengan 2 hash buckets, untuk digunakan dalam konteks interaktif dalam pipeline deteksi stres.

In [6]:
output = example_gen_pb2.Output(
    split_config = example_gen_pb2.SplitConfig(splits=[
        example_gen_pb2.SplitConfig.Split(name="train", hash_buckets=8),
        example_gen_pb2.SplitConfig.Split(name="eval", hash_buckets=2)
    ])
)
example_gen = CsvExampleGen(input_base=DATA_ROOT, output_config=output)

In [7]:
interactive_context.run(example_gen)

c:\Users\ANANG\ML_Ops\myenv\lib\site-packages\setuptools\distutils_patch.py:25: UserWarning: Distutils was imported before Setuptools. This usage is discouraged and may exhibit undesirable behaviors or errors. Please use Setuptools' objects directly or at least import Setuptools first.
  warnings.warn(


ExecutionResult(
    component_id: CsvExampleGen
    execution_id: 26
    outputs:
        examples: OutputChannel(artifact_type=Examples, producer_component_id=CsvExampleGen, output_key=examples, additional_properties={}, additional_custom_properties={}))

### StatisticGen
Code ini menjalankan `StatisticsGen` untuk menghasilkan statistik deskriptif dari data yang dihasilkan oleh `example_gen` dalam konteks interaktif pada pipeline deteksi stres.

In [8]:
statistics_gen = StatisticsGen(
    examples=example_gen.outputs["examples"]
)
 
 
interactive_context.run(statistics_gen)

ExecutionResult(
    component_id: StatisticsGen
    execution_id: 27
    outputs:
        statistics: OutputChannel(artifact_type=ExampleStatistics, producer_component_id=StatisticsGen, output_key=statistics, additional_properties={}, additional_custom_properties={}))

Code ini akan menampilkan output statistik yang dihasilkan oleh komponen `StatisticsGen` dari pipeline deteksi stres dalam konteks interaktif.

In [9]:
interactive_context.show(statistics_gen.outputs["statistics"])

### SchemaGen
Code ini digunakan untuk menjalankan komponen `SchemaGen` dalam pipeline deteksi stres, yang menghasilkan skema data berdasarkan statistik yang dihasilkan sebelumnya oleh komponen `StatisticsGen`.

In [10]:
schema_gen = SchemaGen(    statistics=statistics_gen.outputs["statistics"]
)
interactive_context.run(schema_gen)

ExecutionResult(
    component_id: SchemaGen
    execution_id: 28
    outputs:
        schema: OutputChannel(artifact_type=Schema, producer_component_id=SchemaGen, output_key=schema, additional_properties={}, additional_custom_properties={}))

Code ini digunakan untuk menampilkan skema yang dihasilkan oleh komponen `SchemaGen` dalam pipeline deteksi stres.

In [11]:
interactive_context.show(schema_gen.outputs["schema"])

Type  Presence Valency Domain
Feature name                                
'Body'        BYTES  required              -
'Headline'    BYTES  required              -
'Label'         INT  required              -
'﻿URLs'       BYTES  required              -

### ExampleValidator
Code ini digunakan untuk menjalankan komponen `ExampleValidator` dalam pipeline deteksi stres, yang akan mengevaluasi contoh data berdasarkan statistik yang dihasilkan dan skema yang didefinisikan sebelumnya.

In [12]:
example_validator = ExampleValidator(
    statistics=statistics_gen.outputs['statistics'],
    schema=schema_gen.outputs['schema']
)
interactive_context.run(example_validator)

ExecutionResult(
    component_id: ExampleValidator
    execution_id: 29
    outputs:
        anomalies: OutputChannel(artifact_type=ExampleAnomalies, producer_component_id=ExampleValidator, output_key=anomalies, additional_properties={}, additional_custom_properties={}))

Code ini digunakan untuk menampilkan anomali yang terdeteksi oleh komponen `ExampleValidator` berdasarkan evaluasi terhadap statistik dan skema yang telah didefinisikan sebelumnya dalam pipeline deteksi stres.

In [13]:
interactive_context.show(example_validator.outputs['anomalies'])

## Data Preprocessing

### Transform
Code ini menginisialisasi dan menjalankan komponen `Transform` dalam pipeline deteksi stres menggunakan TFX. Komponen ini bertanggung jawab untuk mengambil contoh data dari `example_gen`, menerapkan transformasi yang didefinisikan dalam modul transformasi yang disediakan, dan menghasilkan output yang telah ditransformasi untuk digunakan dalam langkah-langkah selanjutnya dari pipeline.

In [14]:
TRANSFORM_MODULE_FILE = "fake_news_transform.py"

In [15]:
%%writefile {TRANSFORM_MODULE_FILE}

import tensorflow as tf

LABEL_KEY = "Label"
FEATURE_KEY = "Headline"


def transformed_name(key):
    """Renaming transformed features"""
    return key + "_xf"


def preprocessing_fn(inputs):
    """
    Preprocess input features into transformed features

    Args:
        inputs: map from feature keys to raw features.

    Return:
        outputs: map from feature keys to transformed features.
    """

    outputs = {}

    outputs[transformed_name(FEATURE_KEY)] = tf.strings.lower(inputs[FEATURE_KEY])

    outputs[transformed_name(LABEL_KEY)] = tf.cast(inputs[LABEL_KEY], tf.int64)

    return outputs


Overwriting fake_news_transform.py


In [16]:
transform = Transform(
    examples=example_gen.outputs['examples'],
    schema=schema_gen.outputs['schema'],
    module_file=os.path.abspath(TRANSFORM_MODULE_FILE)
)
interactive_context.run(transform)

Instructions for updating:
Use ref() instead.


Instructions for updating:
Use ref() instead.


INFO:tensorflow:Assets written to: pipelines\jericho_luthfi_ihFK-pipeline\Transform\transform_graph\30\.temp_path\tftransform_tmp\6f00f0f209f7481c9470c51a3c6edc04\assets


INFO:tensorflow:Assets written to: pipelines\jericho_luthfi_ihFK-pipeline\Transform\transform_graph\30\.temp_path\tftransform_tmp\6f00f0f209f7481c9470c51a3c6edc04\assets


INFO:tensorflow:struct2tensor is not available.


...

INFO:tensorflow:tensorflow_decision_forests is not available.


INFO:tensorflow:tensorflow_decision_forests is not available.


INFO:tensorflow:tensorflow_text is not available.


INFO:tensorflow:tensorflow_text is not available.


ExecutionResult(
    component_id: Transform
    execution_id: 30
    outputs:
        transform_graph: OutputChannel(artifact_type=TransformGraph, producer_component_id=Transform, output_key=transform_graph, additional_properties={}, additional_custom_properties={})
        transformed_examples: OutputChannel(artifact_type=Examples, producer_component_id=Transform, output_key=transformed_examples, additional_properties={}, additional_custom_properties={})
        updated_analyzer_cache: OutputChannel(artifact_type=TransformCache, producer_component_id=Transform, output_key=updated_analyzer_cache, additional_properties={}, additional_custom_properties={})
        pre_transform_schema: OutputChannel(artifact_type=Schema, producer_component_id=Transform, output_key=pre_transform_schema, additional_properties={}, additional_custom_properties={})
        pre_transform_stats: OutputChannel(artifact_type=ExampleStatistics, producer_component_id=Transform, output_key=pre_transform_stats, additional_properties={}, additional_custom_properties={})
        post_transform_schema: OutputChannel(artifact_type=Schema, producer_component_id=Transform, output_key=post_transform_schema, additional_properties={}, additional_custom_properties={})
        post_transform_stats: OutputChannel(artifact_type=ExampleStatistics, producer_component_id=Transform, output_key=post_transform_stats, additional_properties={}, additional_custom_properties={})
        post_transform_anomalies: OutputChannel(artifact_type=ExampleAnomalies, producer_component_id=Transform, output_key=post_transform_anomalies, additional_properties={}, additional_custom_properties={}))

### Tuner
Code ini menginisialisasi dan menjalankan komponen `Tuner` dalam pipeline deteksi stres menggunakan TFX. Komponen ini bertanggung jawab untuk melakukan penyetelan parameter model menggunakan `Hyperband` tuner dengan definisi model yang disesuaikan berdasarkan modul tuner yang diberikan. Hyperparameter tuning dilakukan berdasarkan metrik `binary_accuracy` dengan penggunaan data yang telah ditransformasi dari `transform.outputs["transformed_examples"]` dan skema yang dihasilkan dari `schema_gen.outputs["schema"]`.

In [17]:
TUNER_MODULE_FILE = "fake_news_tuner.py"

In [18]:
%%writefile {TUNER_MODULE_FILE}

from typing import Any, Dict, NamedTuple, Text
import keras_tuner as kt
import tensorflow as tf
import tensorflow_transform as tft
from keras_tuner.engine import base_tuner
from tensorflow.keras import layers
from tfx.components.trainer.fn_args_utils import FnArgs

LABEL_KEY = "Label"
FEATURE_KEY = "Headline"
NUM_EPOCHS = 5

# Define parameter tuning with early stopping callbacks
TunerResult = NamedTuple(
    "TunerFnResult", [("tuner", base_tuner.BaseTuner), ("fit_kwargs", Dict[Text, Any])]
)
es = tf.keras.callbacks.EarlyStopping(
    monitor="val_binary_accuracy",
    mode="max",
    verbose=1,
    patience=10,
    restore_best_weights=True,
)


# Create utilities function
def transformed_name(key):
    """Renaming transformed features"""
    return key + "_xf"


def gzip_reader_fn(filenames):
    return tf.data.TFRecordDataset(filenames, compression_type="GZIP")


def input_fn(
    file_pattern, tf_transform_output, num_epochs, batch_size=64
) -> tf.data.Dataset:
    """Get post_transform feature & create batches of data"""

    # Get post_transform feature spec
    transform_feature_spec = tf_transform_output.transformed_feature_spec().copy()

    # create batches of data
    dataset = tf.data.experimental.make_batched_features_dataset(
        file_pattern=file_pattern,
        batch_size=batch_size,
        features=transform_feature_spec,
        reader=gzip_reader_fn,
        num_epochs=num_epochs,
        label_key=transformed_name(LABEL_KEY),
    )
    return dataset


def model_builder(hp, vectorizer):
    """
    Builds the model and sets up the hyperparameters to tune.
    """

    ## Define parameter used for tuning model
    n_layers = hp.Int("n_layers", min_value=1, max_value=5, step=1)
    embedding_dim = hp.Int("embedding_dim", min_value=16, max_value=128, step=32)
    lstm_units = hp.Int("lstm_units", min_value=32, max_value=128, step=32)
    fc_units = hp.Int("fc_units", min_value=16, max_value=64, step=16)
    lr = hp.Choice("lr", values=[1e-2, 1e-3, 1e-4])

    inputs = tf.keras.Input(
        shape=(1,), name=transformed_name(FEATURE_KEY), dtype=tf.string
    )

    x = vectorizer(inputs)
    x = layers.Embedding(5_000, embedding_dim, name="embedding")(x)
    x = layers.Dropout(0.2)(x)
    x = layers.Bidirectional(layers.LSTM(lstm_units))(x)

    for _ in range(n_layers):
        x = layers.Dense(fc_units, activation="relu")(x)

    x = layers.Dropout(0.2)(x)
    outputs = layers.Dense(1, activation="sigmoid")(x)

    model = tf.keras.Model(inputs=inputs, outputs=outputs)

    model.compile(
        loss=tf.keras.losses.BinaryCrossentropy(),
        optimizer=tf.keras.optimizers.Adam(lr),
        metrics=[tf.keras.metrics.BinaryAccuracy()],
    )

    # print(model)
    model.summary()
    return model


def tuner_fn(fn_args: FnArgs):
    # Ensure transform_graph_path is correct
    tf_output = tft.TFTransformOutput(fn_args.transform_graph_path)

    # Ensure train_files and eval_files paths are correct
    train_set = input_fn(fn_args.train_files[0], tf_output, NUM_EPOCHS)
    eval_set = input_fn(fn_args.eval_files[0], tf_output, NUM_EPOCHS)

    # Adapt vectorizer to the training dataset
    vectorize_layer = layers.TextVectorization(
        max_tokens=5_000,
        output_mode="int",
        output_sequence_length=500,
    )
    vectorize_layer.adapt(train_set.map(lambda x, _: x[transformed_name(FEATURE_KEY)]))

    # Define tuner search strategy
    tuner = kt.Hyperband(
        hypermodel=lambda hp: model_builder(hp, vectorize_layer),
        objective=kt.Objective("binary_accuracy", direction="max"),
        max_epochs=NUM_EPOCHS,
        factor=3,
        directory=fn_args.working_dir,
        project_name="kt_hyperband",
    )

    return TunerResult(
        tuner=tuner,
        fit_kwargs={
            "callbacks": [es],
            "x": train_set,
            "validation_data": eval_set,
            "steps_per_epoch": fn_args.train_steps,
            "validation_steps": fn_args.eval_steps,
        },
    )


Writing fake_news_tuner.py


In [19]:
from tfx.proto import example_gen_pb2, pusher_pb2, trainer_pb2

tuner = Tuner(
    module_file=TUNER_MODULE_FILE,
    examples=transform.outputs["transformed_examples"],
    transform_graph=transform.outputs["transform_graph"],
    schema=schema_gen.outputs["schema"],
    train_args=trainer_pb2.TrainArgs(splits=["train"], num_steps=20),
    eval_args=trainer_pb2.EvalArgs(splits=["eval"], num_steps=10),
)

interactive_context.run(tuner)

Trial 10 Complete [00h 00m 55s]
binary_accuracy: 0.805468738079071

Best binary_accuracy So Far: 0.9390624761581421
Total elapsed time: 00h 15m 59s
INFO:tensorflow:Oracle triggered exit


INFO:tensorflow:Oracle triggered exit


Results summary
Results in pipelines\jericho_luthfi_ihFK-pipeline\.temp\31\kt_hyperband
Showing 10 best trials
Trial summary
Hyperparameters:
n_layers: 4
embedding_dim: 80
lstm_units: 64
fc_units: 64
lr: 0.01
tuner/epochs: 5
tuner/initial_epoch: 0
tuner/bracket: 0
tuner/round: 0
Score: 0.9390624761581421
Trial summary
Hyperparameters:
n_layers: 3
embedding_dim: 48
lstm_units: 64
fc_units: 48
lr: 0.001
tuner/epochs: 5
tuner/initial_epoch: 0
tuner/bracket: 0
tuner/round: 0
Score: 0.87890625
Trial summary
Hyperparameters:
n_layers: 5
embedding_dim: 112
lstm_units: 64
fc_units: 32
lr: 0.01
tuner/epochs: 5
tuner/initial_epoch: 2
tuner/bracket: 1
tuner/round: 1
tuner/trial_id: 0002
Score: 0.85546875
Trial summary
Hyperparameters:
n_layers: 4
embedding_dim: 112
lstm_units: 32
fc_units: 48
lr: 0.001
tuner/epochs: 5
tuner/initial_epoch: 2
tuner/bracket: 1
tuner/round: 1
tuner/trial_id: 0003
Score: 0.8203125
Trial summary
Hyperparameters:
n_layers: 5
embedding_dim: 16
lstm_units: 32
fc_units: 32

ExecutionResult(
    component_id: Tuner
    execution_id: 31
    outputs:
        best_hyperparameters: OutputChannel(artifact_type=HyperParameters, producer_component_id=Tuner, output_key=best_hyperparameters, additional_properties={}, additional_custom_properties={})
        tuner_results: OutputChannel(artifact_type=TunerResults, producer_component_id=Tuner, output_key=tuner_results, additional_properties={}, additional_custom_properties={}))

### Trainer
Code ini berfungsi sebagai modul trainer untuk melatih model machine learning dalam pipeline deteksi stres menggunakan TensorFlow Extended (TFX). Modul ini membangun model berdasarkan parameter yang diatur, melatihnya dengan data yang telah ditransformasi, dan menyimpan model yang telah dilatih ke dalam direktori `serving_model_dir`. Kemudian, modul trainer dijalankan dalam konteks interaktif TFX untuk melatih dan mengevaluasi model menggunakan data yang telah dipisahkan ke dalam subset train dan eval berdasarkan konfigurasi yang diberikan.

In [20]:
TRAINER_MODULE_FILE = "fake_news_trainer.py"

In [21]:
%%writefile {TRAINER_MODULE_FILE}

import os
import tensorflow as tf
import tensorflow_transform as tft
from tensorflow.keras import layers
from tfx.components.trainer.fn_args_utils import FnArgs

LABEL_KEY = "Label"
FEATURE_KEY = "Headline"


def transformed_name(key):
    """Renaming transformed features"""
    return key + "_xf"


def gzip_reader_fn(filenames):
    """Loads compressed data"""
    return tf.data.TFRecordDataset(filenames, compression_type="GZIP")


def input_fn(
    file_pattern, tf_transform_output, num_epochs, batch_size=64
) -> tf.data.Dataset:
    """Get post_tranform feature & create batches of data"""

    # Get post_transform feature spec
    transform_feature_spec = tf_transform_output.transformed_feature_spec().copy()

    # create batches of data
    dataset = tf.data.experimental.make_batched_features_dataset(
        file_pattern=file_pattern,
        batch_size=batch_size,
        features=transform_feature_spec,
        reader=gzip_reader_fn,
        num_epochs=num_epochs,
        label_key=transformed_name(LABEL_KEY),
    )
    return dataset


def model_builder(hp, vectorizer):
    """Build machine learning model"""
    inputs = tf.keras.Input(
        shape=(1,), name=transformed_name(FEATURE_KEY), dtype=tf.string
    )

    x = vectorizer(inputs)
    x = layers.Embedding(5_000, hp.get("embedding_dim"), name="embedding")(x)
    x = layers.Dropout(0.2)(x)
    x = layers.Bidirectional(layers.LSTM(hp.get("lstm_units")))(x)

    for _ in range(hp.get("n_layers")):
        x = layers.Dense(hp.get("fc_units"), activation="relu")(x)

    x = layers.Dropout(0.2)(x)
    outputs = layers.Dense(1, activation="sigmoid")(x)

    model = tf.keras.Model(inputs=inputs, outputs=outputs)

    model.compile(
        loss="binary_crossentropy",
        optimizer=tf.keras.optimizers.Adam(hp.get("lr")),
        metrics=[tf.keras.metrics.BinaryAccuracy()],
    )

    model.summary()
    return model


def _get_serve_tf_examples_fn(model, tf_transform_output):
    model.tft_layer = tf_transform_output.transform_features_layer()

    @tf.function
    def serve_tf_examples_fn(serialized_tf_examples):
        feature_spec = tf_transform_output.raw_feature_spec()

        feature_spec.pop(LABEL_KEY)

        parsed_features = tf.io.parse_example(serialized_tf_examples, feature_spec)

        transformed_features = model.tft_layer(parsed_features)

        # get predictions using the transformed features
        return model(transformed_features)

    return serve_tf_examples_fn


def run_fn(fn_args: FnArgs) -> None:
    log_dir = os.path.join(os.path.dirname(fn_args.serving_model_dir), "logs")

    tensorboard_callback = tf.keras.callbacks.TensorBoard(
        log_dir=log_dir, update_freq="batch"
    )

    es = tf.keras.callbacks.EarlyStopping(
        monitor="val_binary_accuracy",
        mode="max",
        verbose=1,
        patience=10,
        restore_best_weights=True,
    )
    mc = tf.keras.callbacks.ModelCheckpoint(
        fn_args.serving_model_dir,
        monitor="val_binary_accuracy",
        mode="max",
        verbose=1,
        save_best_only=True,
    )

    # Debugging: Log the contents of fn_args
    print("fn_args:", fn_args)
    
    # Check if hyperparameters are present
    if fn_args.hyperparameters:
        hp = fn_args.hyperparameters.get("values")
    else:
        # Set default hyperparameters if not present
        hp = {
            "embedding_dim": 64,
            "lstm_units": 64,
            "n_layers": 2,
            "fc_units": 32,
            "lr": 0.001,
            "tuner/epochs": 5,
        }

    # Load the transform output
    tf_transform_output = tft.TFTransformOutput(fn_args.transform_graph_path)

    # Create batches of data
    train_set = input_fn(
        fn_args.train_files, tf_transform_output, hp.get("tuner/epochs")
    )
    val_set = input_fn(fn_args.eval_files, tf_transform_output, hp.get("tuner/epochs"))
    vectorize_layer = layers.TextVectorization(
        max_tokens=5_000,
        output_mode="int",
        output_sequence_length=500,
    )
    vectorize_layer.adapt(train_set.map(lambda x, _: x[transformed_name(FEATURE_KEY)]))

    # Build the model
    model = model_builder(hp, vectorize_layer)

    # Train the model
    model.fit(
        x=train_set,
        validation_data=val_set,
        callbacks=[tensorboard_callback, es, mc],
        steps_per_epoch=fn_args.train_steps,
        validation_steps=fn_args.eval_steps,
        epochs=hp.get("tuner/epochs"),
    )
    signatures = {
        "serving_default": _get_serve_tf_examples_fn(
            model, tf_transform_output
        ).get_concrete_function(
            tf.TensorSpec(shape=[None], dtype=tf.string, name="examples")
        )
    }
    
    model.save(fn_args.serving_model_dir, save_format="tf", signatures=signatures)


Writing fake_news_trainer.py


In [22]:
from tfx.proto import trainer_pb2

trainer = Trainer(
    module_file=os.path.abspath(TRAINER_MODULE_FILE),
    examples=transform.outputs['transformed_examples'],
    transform_graph=transform.outputs['transform_graph'],
    schema=schema_gen.outputs['schema'],
    train_args=trainer_pb2.TrainArgs(splits=['train']),
    eval_args=trainer_pb2.EvalArgs(splits=['eval'])
)

interactive_context.run(trainer)

fn_args: FnArgs(working_dir=None, train_files=['pipelines\\jericho_luthfi_ihFK-pipeline\\Transform\\transformed_examples\\30\\Split-train\\*'], eval_files=['pipelines\\jericho_luthfi_ihFK-pipeline\\Transform\\transformed_examples\\30\\Split-eval\\*'], train_steps=None, eval_steps=None, schema_path='pipelines\\jericho_luthfi_ihFK-pipeline\\SchemaGen\\schema\\28\\schema.pbtxt', schema_file='pipelines\\jericho_luthfi_ihFK-pipeline\\SchemaGen\\schema\\28\\schema.pbtxt', transform_graph_path='pipelines\\jericho_luthfi_ihFK-pipeline\\Transform\\transform_graph\\30', transform_output='pipelines\\jericho_luthfi_ihFK-pipeline\\Transform\\transform_graph\\30', data_accessor=DataAccessor(tf_dataset_factory=<function get_tf_dataset_factory_from_artifact.<locals>.dataset_factory at 0x000002527C8E3940>, record_batch_factory=<function get_record_batch_factory_from_artifact.<locals>.record_batch_factory at 0x0000025200F36940>, data_view_decode_fn=None), serving_model_dir='pipelines\\jericho_luthfi_ihF

INFO:tensorflow:Assets written to: pipelines\jericho_luthfi_ihFK-pipeline\Trainer\model\32\Format-Serving\assets


INFO:tensorflow:Assets written to: pipelines\jericho_luthfi_ihFK-pipeline\Trainer\model\32\Format-Serving\assets


254/254 [==============================] - 265s 1s/step - loss: 0.2458 - binary_accuracy: 0.8751 - val_loss: 0.6343 - val_binary_accuracy: 0.8566
Epoch 2/5
254/254 [==============================] - ETA: 0s - loss: 0.0089 - binary_accuracy: 0.9978
Epoch 2: val_binary_accuracy did not improve from 0.85658
254/254 [==============================] - 581s 2s/step - loss: 0.0089 - binary_accuracy: 0.9978 - val_loss: 0.8912 - val_binary_accuracy: 0.8227
Epoch 3/5
254/254 [==============================] - ETA: 0s - loss: 0.0056 - binary_accuracy: 0.9984
Epoch 3: val_binary_accuracy did not improve from 0.85658
254/254 [==============================] - 621s 2s/step - loss: 0.0056 - binary_accuracy: 0.9984 - val_loss: 0.8244 - val_binary_accuracy: 0.8475
Epoch 4/5
254/254 [==============================] - ETA: 0s - loss: 0.0026 - binary_accuracy: 0.9996
Epoch 4: val_binary_accuracy did not improve from 0.85658
254/254 [==============================] - 604s 2s/step - loss: 0.0026 - binary_ac

INFO:tensorflow:struct2tensor is not available.


...

INFO:tensorflow:tensorflow_text is not available.


INFO:tensorflow:tensorflow_text is not available.


INFO:tensorflow:Assets written to: pipelines\jericho_luthfi_ihFK-pipeline\Trainer\model\32\Format-Serving\assets


INFO:tensorflow:Assets written to: pipelines\jericho_luthfi_ihFK-pipeline\Trainer\model\32\Format-Serving\assets


ExecutionResult(
    component_id: Trainer
    execution_id: 32
    outputs:
        model: OutputChannel(artifact_type=Model, producer_component_id=Trainer, output_key=model, additional_properties={}, additional_custom_properties={})
        model_run: OutputChannel(artifact_type=ModelRun, producer_component_id=Trainer, output_key=model_run, additional_properties={}, additional_custom_properties={}))

### Resolver
Code ini menentukan resolver untuk memilih blessed model terbaru dalam konteks TFX menggunakan strategi `LatestBlessedModelStrategy`, sehingga dapat digunakan dalam tahap selanjutnya dalam pipeline.

In [23]:
from tfx.dsl.components.common.resolver import Resolver 
from tfx.dsl.input_resolution.strategies.latest_blessed_model_strategy import LatestBlessedModelStrategy 
from tfx.types import Channel 
from tfx.types.standard_artifacts import Model, ModelBlessing 
 
model_resolver = Resolver(
    strategy_class= LatestBlessedModelStrategy,
    model = Channel(type=Model),
    model_blessing = Channel(type=ModelBlessing)
).with_id('Latest_blessed_model_resolver')
 
interactive_context.run(model_resolver)

ExecutionResult(
    component_id: Latest_blessed_model_resolver
    execution_id: 33
    outputs:
        model: OutputChannel(artifact_type=Model, producer_component_id=Latest_blessed_model_resolver, output_key=model, additional_properties={}, additional_custom_properties={})
        model_blessing: OutputChannel(artifact_type=ModelBlessing, producer_component_id=Latest_blessed_model_resolver, output_key=model_blessing, additional_properties={}, additional_custom_properties={}))

### Evaluator
Code ini mendefinisikan konfigurasi evaluasi untuk TensorFlow Model Analysis (TFMA), termasuk spesifikasi model, spesifikasi slicing, dan metrik yang akan dievaluasi seperti jumlah contoh, AUC, dan metrik klasifikasi biner lainnya dengan ambang batas tertentu untuk akurasi biner.

In [26]:
import tensorflow_model_analysis as tfma 
 
eval_config = tfma.EvalConfig(
    model_specs=[tfma.ModelSpec(label_key="Label")],
    slicing_specs=[tfma.SlicingSpec()],
    metrics_specs=[
        tfma.MetricsSpec(
            metrics=[
                tfma.MetricConfig(class_name="ExampleCount"),
                tfma.MetricConfig(class_name="AUC"),
                tfma.MetricConfig(class_name="FalsePositives"),
                tfma.MetricConfig(class_name="TruePositives"),
                tfma.MetricConfig(class_name="FalseNegatives"),
                tfma.MetricConfig(class_name="TrueNegatives"),
                tfma.MetricConfig(
                    class_name="BinaryAccuracy",
                    threshold=tfma.MetricThreshold(
                        value_threshold=tfma.GenericValueThreshold(
                            lower_bound={"value": 0.5}
                        ),
                        change_threshold=tfma.GenericChangeThreshold(
                            direction=tfma.MetricDirection.HIGHER_IS_BETTER,
                            absolute={"value": 0.0001},
                        ),
                    ),
                ),
            ]
        )
    ],
)

In [27]:
from tfx.components import Evaluator
evaluator = Evaluator(
    examples=example_gen.outputs['examples'],
    model=trainer.outputs['model'],
    baseline_model=model_resolver.outputs['model'],
    eval_config=eval_config)
 
interactive_context.run(evaluator)

Instructions for updating:
Use eager execution and: 
`tf.data.TFRecordDataset(path)`


Instructions for updating:
Use eager execution and: 
`tf.data.TFRecordDataset(path)`


ExecutionResult(
    component_id: Evaluator
    execution_id: 35
    outputs:
        evaluation: OutputChannel(artifact_type=ModelEvaluation, producer_component_id=Evaluator, output_key=evaluation, additional_properties={}, additional_custom_properties={})
        blessing: OutputChannel(artifact_type=ModelBlessing, producer_component_id=Evaluator, output_key=blessing, additional_properties={}, additional_custom_properties={}))

In [28]:
# Visualize the evaluation results
eval_result = evaluator.outputs['evaluation'].get()[0].uri
tfma_result = tfma.load_eval_result(eval_result)
tfma.view.render_slicing_metrics(tfma_result)
tfma.addons.fairness.view.widget_view.render_fairness_indicator(
    tfma_result
)

FairnessIndicatorViewer(slicingMetrics=[{'sliceValue': 'Overall', 'slice': 'Overall', 'metrics': {'binary_accu…

## Model Deployment

### Pusher
Code ini melakukan push model yang telah dilatih dan divalidasi ke direktori yang disebutkan dalam `push_destination`. Setelah push berhasil, kode mengirimkan permintaan HTTP GET ke endpoint TensorFlow Serving untuk mendapatkan informasi model yang telah di-push.

In [29]:
from tfx.components import Pusher 
from tfx.proto import pusher_pb2 
 
pusher = Pusher(
model=trainer.outputs['model'],
model_blessing=evaluator.outputs['blessing'],
push_destination=pusher_pb2.PushDestination(
    filesystem=pusher_pb2.PushDestination.Filesystem(
        base_directory='serving_model_dir/fake-news-model'))
 
)
 
interactive_context.run(pusher)

ExecutionResult(
    component_id: Pusher
    execution_id: 36
    outputs:
        pushed_model: OutputChannel(artifact_type=PushedModel, producer_component_id=Pusher, output_key=pushed_model, additional_properties={}, additional_custom_properties={}))

In [30]:
import requests
from pprint import PrettyPrinter
 
pp = PrettyPrinter()
pp.pprint(requests.get("http://localhost:8080/v1/models/fake-news-model").json())

{'model_version_status': [{'state': 'AVAILABLE',
                           'status': {'error_code': 'OK', 'error_message': ''},
                           'version': '1721214660'}]}
